## Code
### Imports

In [17]:
import os
import numpy as np
import pandas as pd
import feather

import matplotlib
import matplotlib.pyplot as plt
from matplotlib import colors as mcolors
from matplotlib import patches as mpatches
import seaborn as sns

import plotly.plotly as pltly
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot, \
                           plot_mpl
from plotly.graph_objs import Scatter3d, Data, Marker, Layout, Figure, Scene, \
                              XAxis, YAxis, ZAxis

In [18]:
COLORS = list(map(mcolors.to_hex, plt.cm.tab20.colors))

init_notebook_mode(connected=True)

### Data loading/processing

In [23]:
def check_for_feather_files(data_dir):
    fnames = ('combined_expr.feather', 'combined_feat.feather', 'combined_samp.feather')
    for fname in fnames:
        if not os.path.exists(os.path.join(data_dir, fname)):
            print(f"File: {fname} doesn't exist!  "
                  "Did you run the `convert_eset_to_feather.R` script?")
            raise IOError("File: {fname} doesn't exist!")

def read_raw_data():
    data_dir = '.'#./../data/raw''
    check_for_feather_files(data_dir)
    
    read_feather = lambda fname: feather.read_dataframe(os.path.join(data_dir, fname))

    expression = read_feather('combined_expr.feather')
    expression.set_index('index', inplace=True)
    features = read_feather('combined_feat.feather')
    features.set_index('index', inplace=True)
    samples = read_feather('combined_samp.feather')
    samples.set_index('index', inplace=True)

    return expression, features, samples

def subsample_raw_data(expression, samples, n=250):
    keep_samples = samples.groupby('tumor.type').apply(lambda x: x.sample(n=n, replace=True))
    keep_samples = keep_samples.drop_duplicates().index.get_level_values(1)

    return expression.loc[:, keep_samples], samples.loc[keep_samples]

def normalize_raw_data(expression, features):
    normed = expression.apply(np.log1p) # apply is *slightly* faster and ln + 1 is MUCH faster than log2 + 1
    row_max = normed.max(axis=1)
    row_std = normed.std(axis=1)
    
    keep_rows = (row_max > 8) & (row_std > 2)
    return normed.loc[keep_rows], features.loc[keep_rows,]

### Dimensionality Reduction

In [24]:
from sklearn.decomposition import PCA
from umap import UMAP
from MulticoreTSNE import MulticoreTSNE

np.random.seed(30308891)

def run_pca(data):
    pca_params = dict()
    pca = PCA(**pca_params)
    
    embedding = pca.fit_transform(data.T.values)
    explained_var = np.cumsum(pca.explained_variance_ratio_) * 100
    
    return embedding[:,:3], explained_var

def run_tsne(data):
    tsne_params = dict(n_components=3, n_iter=3000, n_jobs=4)
    embedding = MulticoreTSNE(**tsne_params).fit_transform(data.T.values)
    
    return embedding, None

def run_umap(data):
    umap_params = dict(n_components=3, metric='euclidean')
    embedding = UMAP(**umap_params).fit_transform(data.T.values)

    return embedding, None

### Plotting

In [25]:
def plot_unmatched_3d(tsne_data, umap_data, pca_data, labels):
    colors = COLORS * 3

    cancer_types = np.unique(labels)
    n_cancers = len(cancer_types)    

    tsne_traces = []
    umap_traces = []
    pca_traces = []
    for data, traces in zip((tsne_data, umap_data, pca_data),
                            (tsne_traces, umap_traces, pca_traces)):
        for k, ctype in enumerate(cancer_types):
            inds = np.argwhere(labels == ctype)[:,0]
            x, y, z = data[inds,:].T
            marker_dict = dict(color=colors[k], size=3, symbol='circle',
                               line=dict(width=0, color=colors[k]))
            trace = Scatter3d(x=x, y=y, z=z, name=ctype, mode='markers',
                              text=[f"Sample: {j}" for j in inds],
                              marker=marker_dict, visible=False)
            traces.append(trace)
    
    tsne_ind = np.repeat([1,0,0], n_cancers).astype(bool).tolist()
    pca_ind = np.repeat([0,1,0], n_cancers).astype(bool).tolist()
    umap_ind = np.repeat([0,0,1], n_cancers).astype(bool).tolist()
    data = Data(tsne_traces + pca_traces + umap_traces, visible=tsne_ind)


    updatemenus = list([
        dict(
            buttons=list([
                dict(
                    args=[dict(visible=pca_ind),
                          dict(title='PCA')],
                    label='PCA',
                    method='update'
                ),
                dict(
                    args=[dict(visible=tsne_ind),
                          dict(title='t-SNE')],
                    label='t-SNE',
                    method='update'
                ),
                dict(
                    args=[dict(visible=umap_ind),
                          dict(title='UMAP')],
                    label='UMAP',
                    method='update'
                )
            ]),
            type='buttons',
            showactive = True,
        ),

    ])
    layout = Layout(title='TCGA Cancer types', hovermode='closest',
                    updatemenus=updatemenus)

    fig = Figure(data=data, layout=layout)
    iplot(fig, filename='test')

In [6]:
def plot_matched_3d(tsne_data, umap_data, pca_data, labels, subtypes):
    # subtypes -> 0 for normal, 1 for cancer
    
    colors = COLORS * 3
    primary_colors = COLORS[::2] * 4
    secondary_colors = COLORS[1::2] * 4

    cancer_types = np.unique(labels)
    n_cancers = len(cancer_types)    

    tsne_traces = []
    umap_traces = []
    pca_traces = []
    for data, traces in zip((tsne_data, umap_data, pca_data),
                            (tsne_traces, umap_traces, pca_traces)):
        for k, ctype in enumerate(cancer_types):
            normal_inds = np.argwhere((labels == ctype) & (subtypes == 0))[:,0]
            cancer_inds = np.argwhere((labels == ctype) & (subtypes == 1))[:,0]

            # can also try different colors but same shape
            normal_markers = dict(color=secondary_colors[k], size=2, symbol='circle',
                                  line=dict(width=0, color=colors[k]))
            cancer_markers = dict(color=primary_colors[k], size=2, symbol='diamond',
                                  line=dict(width=0, color=colors[k]))
            
            x, y, z = data[normal_inds,:].T
            normal_trace = Scatter3d(x=x, y=y, z=z, name=f'{ctype} N', mode='markers',
                                     text=[f"Sample: {j}" for j in normal_inds],
                                     marker=normal_markers, visible=False,
                                     legendgroup=ctype, showlegend=True)
            
            x, y, z = data[cancer_inds,:].T
            cancer_trace = Scatter3d(x=x, y=y, z=z, name=f'{ctype} T', mode='markers',
                                     text=[f"Sample: {j}" for j in cancer_inds],
                                     marker=cancer_markers, visible=False,
                                     legendgroup=ctype, showlegend=True)
            traces.append(normal_trace)
            traces.append(cancer_trace)
    
    tsne_ind = np.repeat([1,0,0], n_cancers*2).astype(bool).tolist()
    pca_ind = np.repeat([0,1,0], n_cancers*2).astype(bool).tolist()
    umap_ind = np.repeat([0,0,1], n_cancers*2).astype(bool).tolist()
    data = Data(tsne_traces + pca_traces + umap_traces)


    updatemenus = list([
        dict(
            buttons=list([
                dict(
                    args=[dict(visible=tsne_ind),
                          dict(title='t-SNE')],
                    label='t-SNE',
                    method='update'
                ),
                dict(
                    args=[dict(visible=pca_ind),
                          dict(title='PCA')],
                    label='PCA',
                    method='update'
                ),
                dict(
                    args=[dict(visible=umap_ind),
                          dict(title='UMAP')],
                    label='UMAP',
                    method='update'
                )
            ]),
            type='buttons',
            showactive = True,
        ),

    ])
    layout = Layout(title='TCGA Cancer types', hovermode='closest',
                    updatemenus=updatemenus)

    fig = Figure(data=data, layout=layout)
    iplot(fig, filename='test')

## Run

Load in the raw data stored in `feather` format, subsample 250 (or fewer) samples from each cancer type, and normalize it.  **Make sure you ran the `convert_eset_to_feather` script first.**

In [22]:
expression, features, samples = read_raw_data()
subsampled, samples = subsample_raw_data(expression, samples)
normed, features = normalize_raw_data(subsampled, features)

In [8]:
print(expression.shape)
print(subsampled.shape)
print(normed.shape)

(20531, 10446)
(20531, 4844)
(1157, 4844)


Compute 

- PCA (`sklearn`),
- t-SNE (`MulticoreTSNE`), and 
- UMAP (`umap-learn`), 

all in 3 dimensions.  PCA also returns the variance explained by all (not just first 3) PCs.

In [9]:
pca_data, pca_var = run_pca(normed)
tsne_data, _ = run_tsne(normed)
umap_data, _ = run_umap(normed)

In [10]:
print(pca_data.shape)
print(tsne_data.shape)
print(umap_data.shape)
print(pca_var[:10])

(4844, 3)
(4844, 3)
(4844, 3)
[20.02811911 31.94419917 39.61923857 44.54056671 49.17568132 52.59862359
 55.09011933 57.28182874 59.42995432 61.34068672]


code|definition|symbol
---|---|---
01|Primary Solid Tumor|TP
02|Recurrent Solid Tumor|TR
03|Primary Blood Derived Cancer - Peripheral Blood|TB
04|Recurrent Blood Derived Cancer - Bone Marrow|TRBM
05|Additional - New Primary|TAP
06|Metastatic|TM
07|Additional Metastatic|TAM
08|Human Tumor Original Cells|THOC
09|Primary Blood Derived Cancer - Bone Marrow|TBM
10|Blood Derived Normal|NB
11|Solid Tissue Normal|NT
12|Buccal Cell Normal|NBC
13|EBV Immortalized Normal|NEBV
14|Bone Marrow Normal|NBM
15|sample type 15|15SH
16|sample type 16|16SH
20|Control Analyte|CELLC
40|Recurrent Blood Derived Cancer - Peripheral Blood|TRB
50|Cell Lines|CELL
60|Primary Xenograft Tissue|XP
61|Cell Line Derived Xenograft Tissue|XCL
99|sample type 99|99SH

Determine sample types from the table above.  Just took the quick and dirty route using `sample.type >= 10`.

In [11]:
labels = samples['tumor.type'].values
sample_types = samples['sample.type'].astype(int).values
sample_types[sample_types >= 10] = 0
sample_types[sample_types > 0] = 1

Two different plotting functions, `matched` and `unmatched`, where the only difference is that `matched` takes into account sample types to differentiate between normal and cancer samples.

The plot starts uninitialized.  Click one of the buttons on the left to determine which dimensionality reduction scheme you would like to plot.  Currently cancers are shown in dark shades and normals are shown in light shades of the same color.

I think the best way to use this plot is to **double click** the legend on one entry so that only that entry is shown.  Then **single click** on another cancer type that you would like to compare it to.  Matched tumor/normals toggle together.

In [12]:
#plot_unmatched_3d(tsne_data, umap_data, pca_data, labels)
plot_matched_3d(tsne_data, umap_data, pca_data, labels, sample_types)

In [16]:
feather.write_dataframe(normed, 'test.feather')